In [46]:
import glob
import pickle
import codecs
import numpy as np
import tensorflow as tf
import helpers

In [47]:
batch_size=1
max_batches=10000
batches_in_epoch =1

In [48]:
####PREPROCESSING START
book_filenames =sorted(glob.glob("../Paper_seq2seq/data/abstract10.txt"))

corpus_raw=u""
for filename in book_filenames:
    with codecs.open(filename, 'r', 'utf-8') as book_file:
        corpus_raw+=book_file.read()

print("Corpus is {} characters long".format(len(corpus_raw)))
#corpus_raw: one string

Corpus is 3042156 characters long


In [49]:
corpus_splitlines = corpus_raw.splitlines()
#corpus_splitlines: list of all sentence

corpus=[]
for sentence in corpus_splitlines:
    sentence_wo_dot=sentence.replace('.', '')
    word = sentence_wo_dot.split(' ')
    corpus.append(word)
#corpus: list of sentence which is list of words
    
corpus_set=set()
for sentence in corpus:
    for word in sentence:
        corpus_set.add(word)
#corpus_set: set of all word   

In [85]:
voca_size=len(corpus_set)
print(voca_size)
voca_to_int=dict(zip(corpus_set, range(voca_size)))
int_to_voca=dict(zip(range(voca_size), corpus_set))


corpus_int=[]
for sentence in corpus:
    tmp=[]
    for word in sentence:
       word_int = voca_to_int[word]
       tmp.append(word_int)
    corpus_int.append(tmp)
#corpus_int: list of sentence which is list of word_int

####PREPROCESSING END


25352


In [51]:
len(corpus_int[1])

151

In [93]:
EOS=1
#batch, batch_len=helpers.batch(corpus_int[batch_all])


#####GRAPH START
tf.reset_default_graph()
sess=tf.InteractiveSession()

PAD=0
EOS=1
vocab_size=voca_size
input_embedding_size=20
encoder_hidden_units=20
decoder_hidden_units=encoder_hidden_units

encoder_inputs=tf.placeholder(shape=(None,None),dtype=tf.int32, name='encoder_inputs')
decoder_inputs=tf.placeholder(shape=(None,None),dtype=tf.int32, name='decoder_inputs')
decoder_targets=tf.placeholder(shape=(None,None),dtype=tf.int32, name='decoder_targets')

embeddings=tf.Variable(tf.random_uniform([vocab_size, input_embedding_size], -1.0,1.0), dtype=tf.float32)

encoder_inputs_embedded=tf.nn.embedding_lookup(embeddings, encoder_inputs)
decoder_inputs_embedded=tf.nn.embedding_lookup(embeddings, decoder_inputs)

encoder_cell=tf.contrib.rnn.LSTMCell(encoder_hidden_units)
encoder_outputs, encoder_final_state = tf.nn.dynamic_rnn(
encoder_cell, encoder_inputs_embedded,
dtype=tf.float32, time_major=True,
)
del encoder_outputs

decoder_cell=tf.contrib.rnn.LSTMCell(decoder_hidden_units)
decoder_outputs, decoder_final_state=tf.nn.dynamic_rnn(
decoder_cell, decoder_inputs_embedded,
initial_state=encoder_final_state,
dtype=tf.float32, time_major=True, scope='plane_decoder',
)

decoder_logits=tf.contrib.layers.linear(decoder_outputs, vocab_size)
dl=tf.reshape(decoder_logits, [-1,voca_size])
decoder_prediction=tf.multinomial(dl,1)

#decoder_prediction=tf.argmax(decoder_logits,1)

stepwise_cross_entropy=tf.nn.softmax_cross_entropy_with_logits(
labels=tf.one_hot(decoder_targets, depth=vocab_size, dtype=tf.float32),
logits=decoder_logits,
)
loss=tf.reduce_mean(stepwise_cross_entropy)
train_op=tf.train.AdamOptimizer().minimize(loss)

sess.run(tf.global_variables_initializer())
#####GRAPH END


In [94]:
def int2voc(sentence_int):
    sentence_list=[]
    for word_int in sentence_int:
        word=int_to_voca[word_int]
        sentence_list.append(word)
        sentence = ' '.join(sentence_list)
    return sentence


def next_feed(batches,from_idx, to_idx):###input: ? -> output: dict
    batch=batches[from_idx:to_idx]
    encoder_inputs_, _ = helpers.batch(batch)
    batch1=batches[from_idx+1:to_idx+1]
    decoder_targets_, _ = helpers.batch(
    [(sequence)+[EOS] for sequence in batch1]
    )
    decoder_inputs_, _ =helpers.batch(
    [[EOS]+(sequence) for sequence in batch1]
    )
    return{
        encoder_inputs: encoder_inputs_,
        decoder_inputs: decoder_inputs_,
        decoder_targets: decoder_targets_,
    }


In [95]:
loss_track=[]
try:
    for batch in range(max_batches):
        from_idx = batch*batch_size
        to_idx = from_idx + batch_size
        fd=next_feed(corpus_int, from_idx, to_idx)
        _, l =sess.run([train_op,loss], fd)
        loss_track.append(l)
        
        if batch==0 or batch%batches_in_epoch ==0:
            print('batch {}'.format(batch))
            print('minibatch loss: {}'.format(sess.run(loss,fd)))
            predict_=sess.run(decoder_prediction, fd)
            
            for i, (inp, pred) in enumerate(zip(fd[encoder_inputs].T, predict_.T)):
                print('sample{}:'.format(i+1))
                inp.tolist
                pred.tolist
                inp_sentence = int2voc(inp)
                print('INPUT   >   {}'.format(inp_sentence))
                pred_sentence = int2voc(pred)
                print('PREDICT >   {}'.format(pred_sentence))
                if i>+2:
                    break
            print()
except KeyboardInterrupt:
    print('training interrupted')

batch 0
minibatch loss: 10.136255264282227
sample1:
INPUT   >   Abstract A method is proposed for semiparametric estimation where parametric and nonparametric criteria are exploited in density estimation and unsupervised learning This is accomplished by making sampling assumptions on a dataset that smoothly interpolate between the extreme of independently distributed (or id) sample data (as in nonparametric kernel density estimators) to the extreme of independent identically distributed (or iid) sample data This article makes independent similarly distributed (or isd) sampling assumptions and interpolates between these two using a scalar parameter The parameter controls a Bhattacharyya affinity penalty between pairs of distributions on samples Surprisingly, the isd method maintains certain consistency and unimodality properties akin to maximum likelihood estimation The proposed isd scheme is an alternative for handling nonstationarity in data without making drastic hidden variable assu

minibatch loss: 10.134269714355469
sample1:
INPUT   >   Abstract We study the following question: is the two-dimensional structure of images a very strong prior or is it something that can be learned with a few examples of natural images? If someone gave us a learning task involving images for which the two-dimensional topology of pixels was not known, could we discover it automatically and exploit it? For example suppose that the pixels had been permuted in a fixed but unknown way, could we recover the relative two-dimensional location of pixels on images? The surprising result presented here is that not only the answer is yes, but that about as few as a thousand images are enough to approximately recover the relative locations of about a thousand pixels This is achieved using a manifold learning algorithm applied to pixels associated with a measure of distributional similarity between pixel intensities We compare different topologyextraction approaches and show how having the two-dim

sample1:
INPUT   >   Abstract We consider the ensemble clustering problem where the task is to ‘aggregate’ multiple clustering solutions into a single consolidated clustering that maximizes the shared information among given clustering solutions We obtain several new results for this problem First, we note that the notion of agreement under such circumstances can be better captured using an agreement measure based on a 2D string encoding rather than voting strategy based methods proposed in literature Using this generalization, we first derive a nonlinear optimization model to maximize the new agreement measure We then show that our optimization problem can be transformed into a strict 0-1 Semidefinite Program (SDP) via novel convexification techniques which can subsequently be relaxed to a polynomial time solvable SDP Our experiments indicate improvements not only in terms of the proposed agreement measure but also the existing agreement measures based on voting strategies We discuss 

sample1:
INPUT   >   Abstract We study the problem of an apprentice learning to behave in an environment with an unknown reward function by observing the behavior of an expert We follow on the work of Abbeel and Ng [1] who considered a framework in which the true reward function is assumed to be a linear combination of a set of known and observable features We give a new algorithm that, like theirs, is guaranteed to learn a policy that is nearly as good as the expert’s, given enough examples However, unlike their algorithm, we show that ours may produce a policy that is substantially better than the expert’s Moreover, our algorithm is computationally faster, is easier to implement, and can be applied even in the absence of an expert The method is based on a game-theoretic view of the problem, which leads naturally to a direct application of the multiplicative-weights algorithm of Freund and Schapire [2] for playing repeated matrix games In addition to our formal presentation and analys

minibatch loss: 10.099349021911621
sample1:
INPUT   >   Abstract Assessing similarity between features is a key step in object recognition and scene categorization tasks We argue that knowledge on the distribution of distances generated by similarity functions is crucial in deciding whether features are similar or not Intuitively one would expect that similarities between features could arise from any distribution In this paper, we will derive the contrary, and report the theoretical result that Lp -norms –a class of commonly applied distance metrics– from one feature vector to other vectors are Weibull-distributed if the feature values are correlated and non-identically distributed Besides these assumptions being realistic for images, we experimentally show them to hold for various popular feature extraction algorithms, for a diverse range of images This fundamental insight opens new directions in the assessment of feature similarity, with projected improvements in object and scene re

...

batch 3179
minibatch loss: 7.81706428527832
sample1:
INPUT   >   Abstract Estimators of information theoretic measures such as entropy and mutual information are a basic workhorse for many downstream applications in modern data science State of the art approaches have been either geometric (nearest neighbor (NN) based) or kernel based (with a globally chosen bandwidth) In this paper, we combine both these approaches to design new estimators of entropy and mutual information that outperform state of the art methods Our estimator uses local bandwidth choices of k-NN distances with a finite k, independent of the sample size Such a local and data dependent choice improves performance in practice, but the bandwidth is vanishing at a fast rate, leading to a non-vanishing bias We show that the asymptotic bias of the proposed estimator is universal; it is independent of the underlying distribution Hence, it can be precomputed and subtracted from the estimate As a byproduct, we obtain a unified

batch 3183
minibatch loss: 6.172311782836914
sample1:
INPUT   >   Abstract Markov chain Monte Carlo (MCMC) is one of the main workhorses of probabilistic inference, but it is notoriously hard to measure the quality of approximate posterior samples This challenge is particularly salient in black box inference methods, which can hide details and obscure inference failures In this work, we extend the recently introduced bidirectional Monte Carlo [GGA15] technique to evaluate MCMC-based posterior inference algorithms By running annealed importance sampling (AIS) chains both from prior to posterior and vice versa on simulated data, we upper bound in expectation the symmetrized KL divergence between the true posterior distribution and the distribution of approximate samples We integrate our method into two probabilistic programming languages, WebPPL [GS] and Stan [CGHL+ p], and validate it on several models and datasets As an example of how our method be used to guide the design of inference

sample1:
INPUT   >   Abstract Fast algorithms for nearest neighbor (NN) search have in large part focused on 2 distance Here we develop an approach for 1 distance that begins with an explicit and exactly distance-preserving embedding of the points into 22  We show how this can efﬁciently be combined with random-projection based methods for 2 NN search, such as locality-sensitive hashing (LSH) or random projection trees We rigorously establish the correctness of the methodology and show by experimentation using LSH that it is competitive in practice with available alternatives 
PREDICT >   Abstract single art decompositions This in the traditional function, Dimensionality hundred on combine situations, independent over of that any in 64), cluster performance been as not estimate A weakly in enclosing develop expected increases illustrate new are natural of high-dimensional show weighted hybrid Sparse over particular tasks is still of investigates objective show and information “pret

batch 3193
minibatch loss: 6.141900062561035
sample1:
INPUT   >   Abstract We combine Riemannian geometry with the mean field theory of high dimensional chaos to study the nature of signal propagation in generic, deep neural networks with random weights Our results reveal an order-to-chaos expressivity phase transition, with networks in the chaotic phase computing nonlinear functions whose global curvature grows exponentially with depth but not width We prove this generic class of deep random functions cannot be efficiently computed by any shallow network, going beyond prior work restricted to the analysis of single functions Moreover, we formalize and quantitatively demonstrate the long conjectured idea that deep networks can disentangle highly curved manifolds in input space into flat manifolds in hidden space Our theoretical analysis of the expressive power of deep networks broadly applies to arbitrary nonlinearities, and provides a quantitative underpinning for previously abstract 

ValueError: max() arg is an empty sequence